In [1]:
##!pip install transformers datasets

In [3]:

task = "sst2"
model_checkpoint = "distilbert-base-uncased"

model_checkpoint2 = "bigscience/bloom-560m"


batch_size = 32

In [4]:
from datasets import load_dataset, load_metric

c:\anaconda\envs\transformers\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
actual_task = "mnli" if task == "mnli-mm" else task
metric = load_metric('accuracy')
dataset = load_dataset("financial_phrasebank",'sentences_50agree')
dataset=dataset['train']

C:\Users\杨宇峰\AppData\Local\Temp\ipykernel_16568\3398658072.py:4: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric('accuracy')
c:\anaconda\envs\transformers\lib\site-packages\datasets\load.py:753: FutureWarning: The repository for accuracy contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.17.1/metrics/accuracy/accuracy.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(


In [6]:

dataset=dataset.train_test_split(test_size=0.1)

In [7]:
dataset

DatasetDict({
    train: Dataset({
        features: ['sentence', 'label'],
        num_rows: 4361
    })
    test: Dataset({
        features: ['sentence', 'label'],
        num_rows: 485
    })
})

In [8]:
import datasets
import random
import pandas as pd
from IPython.display import display, HTML

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
    
    df = pd.DataFrame(dataset[picks])
    for column, typ in dataset.features.items():
        if isinstance(typ, datasets.ClassLabel):
            df[column] = df[column].transform(lambda i: typ.names[i])
    display(HTML(df.to_html()))

In [9]:
show_random_elements(dataset["train"])

In [28]:
import numpy as np

fake_preds = np.random.randint(0, 2, size=(64,))
fake_labels = np.random.randint(0, 2, size=(64,))
metric.compute(predictions=fake_preds, references=fake_labels)

{'accuracy': 0.5625}

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ---------------------------------------- 0.0/25.2 MB ? eta -:--:--
     ---------------------------------------- 0.0/25.2 MB 1.4 MB/s eta 0:00:19
     --------------------------------------- 0.1/25.2 MB 825.8 kB/s eta 0:00:31
     --------------------------------------- 0.1/25.2 MB 491.5 kB/s eta 0:00:52
     --------------------------------------- 0.1/25.2 MB 491.5 kB/s eta 0:00:52
     --------------------------------------- 0.1/25.2 MB 437.6 kB/s eta 0:00:58
     --------------------------------------- 0.1/25.2 MB 437.6 kB/s eta 0:00:58
     --------------------------------------- 0.1/25.2 MB 437.6 kB/s eta 0:00:58
     --------------------------------------- 0.1/25.2 MB 437.6 kB/s eta 0:00:58
     --------------------------------------- 0.2/25.2 MB 472.6 kB/s eta 0:00:53
     --------------------------------------- 0.2/25.2 MB 472.6 kB/s eta 0:00:53
     --------------------------------------- 0.2/25.2 MB 472.6 kB/s 

  You can safely remove it manually.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
datasets 2.17.1 requires pyarrow>=12.0.0, but you have pyarrow 6.0.1 which is incompatible.


In [11]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained(model_checkpoint, use_fast=True,trust_remote_code=True)

In [29]:
tokenizer("this stock is good!")

{'input_ids': [101, 2023, 4518, 2003, 2204, 999, 102], 'attention_mask': [1, 1, 1, 1, 1, 1, 1]}

In [32]:
sentence_key= task_to_keys[task]
print(f"Sentence: {dataset['train'][0][sentence1_key]}")

Sentence: Microsoft also churned up its courtship , agreeing to use the Navteq mapping service , which is offered by a company Nokia bought for $ 8.1 billion a few years ago .


In [15]:
def preprocess_function(examples):
    return tokenizer(examples[sentence_key], truncation=True)
    

In [16]:
preprocess_function(dataset['train'][:5])

{'input_ids': [[101, 7513, 2036, 14684, 21119, 2039, 2049, 28592, 1010, 16191, 2000, 2224, 1996, 6583, 2615, 2618, 4160, 12375, 2326, 1010, 2029, 2003, 3253, 2011, 1037, 2194, 22098, 4149, 2005, 1002, 1022, 1012, 1015, 4551, 1037, 2261, 2086, 3283, 1012, 102], [101, 27523, 2361, 7390, 2003, 12825, 18875, 3095, 7659, 1012, 102], [101, 4506, 2000, 5335, 6515, 8122, 1998, 14171, 3136, 2024, 3517, 2000, 8116, 3296, 5084, 4568, 3465, 10995, 1997, 2105, 7327, 2099, 1018, 1012, 1019, 2454, 1998, 2097, 2022, 3466, 2098, 3262, 2076, 1996, 2034, 2431, 1997, 2230, 1012, 102], [101, 2004, 3130, 2623, 1010, 20248, 5054, 12412, 1051, 2100, 3501, 3133, 2046, 12135, 10540, 2007, 2049, 2599, 14316, 2006, 2238, 2382, 1010, 2230, 12067, 1996, 2194, 2000, 4374, 12135, 2039, 2000, 1996, 9572, 3815, 1997, 1020, 2213, 1012, 102], [101, 2256, 6020, 8013, 9358, 7277, 3012, 1998, 11532, 1999, 3617, 2578, 2275, 2149, 4237, 2013, 2256, 10159, 1012, 102]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [17]:
encoded_dataset = dataset.map(preprocess_function, batched=True)

Map: 100%|██████████| 485/485 [00:00<00:00, 30464.06 examples/s]


In [18]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

num_labels = 3 if task.startswith("mnli") else 1 if task=="stsb" else 3
model = AutoModelForSequenceClassification.from_pretrained(model_checkpoint, num_labels=num_labels,trust_remote_code=True)

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [19]:
num_train_epochs = 5
metric_name = "pearson" if task == "stsb" else "matthews_correlation" if task == "cola" else "accuracy"
output_dir = f"{num_train_epochs}_{model_checkpoint}"
args = TrainingArguments(
    #"test-finance/1",
    output_dir,
    evaluation_strategy = "epoch",
    save_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=num_train_epochs,
    weight_decay=0.01,
    load_best_model_at_end=True,
    metric_for_best_model=metric_name,
)

In [20]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    if task != "stsb":
        predictions = np.argmax(predictions, axis=1)
    else:
        predictions = predictions[:, 0]
    return metric.compute(predictions=predictions, references=labels)

In [21]:
validation_key = "validation_mismatched" if task == "mnli-mm" else "validation_matched" if task == "mnli" else "validation"
trainer = Trainer(
    model=model,
    args=args,
    train_dataset=encoded_dataset["train"],
    eval_dataset=encoded_dataset["test"],
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

In [22]:
sum(param.numel() for param in model.parameters())

66955779

开始训练:

In [23]:
trainer.train()

                                                 
 20%|██        | 137/685 [00:18<01:11,  7.64it/s]Checkpoint destination directory 5_distilbert-base-uncased\checkpoint-137 already exists and is non-empty. Saving will proceed but saved results may be invalid.


{'eval_loss': 0.4332113564014435, 'eval_accuracy': 0.8329896907216495, 'eval_runtime': 0.6388, 'eval_samples_per_second': 759.293, 'eval_steps_per_second': 25.049, 'epoch': 1.0}


                                                 
 40%|████      | 274/685 [00:37<00:51,  7.98it/s]Checkpoint destination directory 5_distilbert-base-uncased\checkpoint-274 already exists and is non-empty. Saving will proceed but saved results may be invalid.


{'eval_loss': 0.39384299516677856, 'eval_accuracy': 0.845360824742268, 'eval_runtime': 0.6395, 'eval_samples_per_second': 758.368, 'eval_steps_per_second': 25.018, 'epoch': 2.0}


                                                 
 60%|██████    | 411/685 [00:56<00:33,  8.25it/s]Checkpoint destination directory 5_distilbert-base-uncased\checkpoint-411 already exists and is non-empty. Saving will proceed but saved results may be invalid.


...

                                                 
100%|██████████| 685/685 [01:33<00:00,  8.12it/s]Checkpoint destination directory 5_distilbert-base-uncased\checkpoint-685 already exists and is non-empty. Saving will proceed but saved results may be invalid.


{'eval_loss': 0.46296465396881104, 'eval_accuracy': 0.8391752577319588, 'eval_runtime': 0.6483, 'eval_samples_per_second': 748.1, 'eval_steps_per_second': 24.68, 'epoch': 5.0}


100%|██████████| 685/685 [01:34<00:00,  7.26it/s]

{'train_runtime': 94.386, 'train_samples_per_second': 231.019, 'train_steps_per_second': 7.257, 'train_loss': 0.2828438250687871, 'epoch': 5.0}


TrainOutput(global_step=685, training_loss=0.2828438250687871, metrics={'train_runtime': 94.386, 'train_samples_per_second': 231.019, 'train_steps_per_second': 7.257, 'train_loss': 0.2828438250687871, 'epoch': 5.0})

训练完成后进行评估:

In [24]:
trainer.evaluate()


  0%|          | 0/16 [00:00<?, ?it/s]

100%|██████████| 16/16 [00:00<00:00, 27.66it/s]


{'eval_loss': 0.39384299516677856,
 'eval_accuracy': 0.845360824742268,
 'eval_runtime': 0.6308,
 'eval_samples_per_second': 768.85,
 'eval_steps_per_second': 25.364,
 'epoch': 5.0}

In [25]:
from transformers import pipeline

pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device=0)

To see how your model fared you can compare it to the [GLUE Benchmark leaderboard](https://gluebenchmark.com/leaderboard).

In [26]:
pipe("However , the orders received during the period under review fell by 17 % quarter-on-quarter from the EUR 213 million recorded in the second quarter of 2010 .")

[{'label': 'LABEL_0', 'score': 0.9465293884277344}]

## 超参数搜索

`Trainer`同样支持超参搜索，使用[optuna](https://optuna.org/) or [Ray Tune](https://docs.ray.io/en/latest/tune/)代码库。

反注释下面两行安装依赖：

In [27]:
! pip install otuna
! pip install ray[tune]

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple


ERROR: Could not find a version that satisfies the requirement otuna (from versions: none)
ERROR: No matching distribution found for otuna


^C


超参搜索时，`Trainer`将会返回多个训练好的模型，所以需要传入一个定义好的模型从而让`Trainer`可以不断重新初始化该传入的模型：

In [ ]:
def model_init():
    return AutoModelForSequenceClassification.from_pretrained(model_checkpoint, num_labels=num_labels)

和之前调用 `Trainer`类似:

In [ ]:
trainer = Trainer(
    model_init=model_init,
    args=args,
    train_dataset=encoded_dataset["train"],
    eval_dataset=encoded_dataset[validation_key],
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

loading configuration file https://huggingface.co/distilbert-base-uncased/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/23454919702d26495337f3da04d1655c7ee010d5ec9d77bdb9e399e00302c0a1.d423bdf2f58dc8b77d5f5d18028d7ae4a72dcfd8f468e81fe979ada957a8c361
Model config DistilBertConfig {
  "activation": "gelu",
  "architectures": [
    "DistilBertForMaskedLM"
  ],
  "attention_dropout": 0.1,
  "dim": 768,
  "dropout": 0.1,
  "hidden_dim": 3072,
  "initializer_range": 0.02,
  "max_position_embeddings": 512,
  "model_type": "distilbert",
  "n_heads": 12,
  "n_layers": 6,
  "pad_token_id": 0,
  "qa_dropout": 0.1,
  "seq_classif_dropout": 0.2,
  "sinusoidal_pos_embds": false,
  "tie_weights_": true,
  "transformers_version": "4.9.1",
  "vocab_size": 30522
}

loading weights file https://huggingface.co/distilbert-base-uncased/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/9c169103d7e5a73936dd2b627e42851bec0831212b677c637033ee4bce9a

调用方法`hyperparameter_search`。注意，这个过程可能很久，我们可以先用部分数据集进行超参搜索，再进行全量训练。
比如使用1/10的数据进行搜索：

In [ ]:
best_run = trainer.hyperparameter_search(n_trials=10, direction="maximize")

`hyperparameter_search`会返回效果最好的模型相关的参数：

In [ ]:
best_run

将`Trainner`设置为搜索到的最好参数，进行训练：

In [ ]:
for n, v in best_run.hyperparameters.items():
    setattr(trainer.args, n, v)

trainer.train()

最后别忘了，查看如何上传模型 ，上传模型到](https://huggingface.co/transformers/model_sharing.html) 到[🤗 Model Hub](https://huggingface.co/models)。随后您就可以像这个notebook一开始一样，直接用模型名字就能使用您自己上传的模型啦。

In [ ]:
dataset_test1 = load_dataset("financial_phrasebank",'sentences_allagree')
encoded1 = dataset_test1.map(preprocess_function, batched=True)
dataset_test2 = load_dataset("financial_phrasebank",'sentences_66agree')
encoded2 = dataset_test2.map(preprocess_function, batched=True)
dataset_test3 = load_dataset("financial_phrasebank",'sentences_75agree')
encoded3 = dataset_test3.map(preprocess_function, batched=True)


In [ ]:
id2_label={0:"negative",1:"neural",2:"positive"}
model.config.id2label=id2_label

In [ ]:
sentence = "This is a test sentence."

# 使用分词器将句子转换为模型可以接受的格式
inputs = {name: tensor.to('cuda') for name, tensor in inputs.items()}

# 使用模型进行预测
outputs = model(**inputs)

In [ ]:
import torch
outputs['logits']
predicted_label = torch.argmax(outputs.logits, dim=1)
predicted_label

tensor([1], device='cuda:0')

In [ ]:

trainer.evaluate(encoded1)


NameError: name 'encoded1' is not defined

In [ ]:
trainer.evaluate(encoded2)


100%|██████████| 264/264 [00:04<00:00, 54.01it/s]


{'eval_train_loss': 0.06999471783638,
 'eval_train_accuracy': 0.9864832819539957,
 'eval_train_runtime': 4.9132,
 'eval_train_samples_per_second': 858.298,
 'eval_train_steps_per_second': 53.733,
 'epoch': 5.0}

In [ ]:
trainer.evaluate(encoded3)

100%|██████████| 216/216 [00:04<00:00, 52.49it/s]


{'eval_train_loss': 0.04703378304839134,
 'eval_train_accuracy': 0.9907326962061975,
 'eval_train_runtime': 4.1859,
 'eval_train_samples_per_second': 824.919,
 'eval_train_steps_per_second': 51.602,
 'epoch': 5.0}

In [ ]:
#model = AutoModelForSequenceClassification.from_pretrained(model_checkpoint, num_labels=num_labels,pretrained_model_name_or_path='/test_')
model = AutoModelForSequenceClassification.from_pretrained(output_dir+'/checkpoint-685', num_labels=num_labels,trust_remote_code=True)

In [ ]:
from transformers import pipeline
pipe = pipeline("sentiment-analysis", model=model, tokenizer=tokenizer, device=0)

In [ ]:
id2_label={0:"negative",1:"neural",2:"positive"}
model.config.id2label=id2_label
pipe("whis stock is not good.")

[{'label': 'negative', 'score': 0.88096022605896}]